<h1 align=center><font size = 5>Segmenting Neighborhoods amoung New York City and Toronto</font></h1>

## Introduction

This is the notebook to collect the neighborhoods data of New York City and Toronto, then use the nearby venus to segment the neighbothoods thruough k-means clustering algorithm.

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in Both City</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    
</font>
</div>

Download all the dependencies that we will need.

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from bs4 import BeautifulSoup # library to parse html from web page
import requests
from IPython.display import display_html

#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


<a id='item1'></a>

## 1. Download and Explore Dataset

New York neighborhood has a total of 5 boroughs and 306 neighborhoods. The dataset is on the following link https://geo.nyu.edu/catalog/nyu_2451_34572

In [3]:
!wget -q -O newyork_data.json https://geo.nyu.edu/download/file/nyu-2451-34572-geojson.json
print('Data downloaded!')

Data downloaded!


#### Load and explore the data of New York

In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

newyork_neighborhoods_data = newyork_data['features']

# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
newyork_neighborhoods = pd.DataFrame(columns=column_names)

for data in newyork_neighborhoods_data:
    borough = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
    
    neighborhood_name = neighborhood_name + ', ' + borough
    
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    newyork_neighborhoods = newyork_neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
newyork_neighborhoods.head()    

Borough        Neighborhood   Latitude  Longitude
0   Bronx    Wakefield, Bronx  40.894705 -73.847201
1   Bronx   Co-op City, Bronx  40.874294 -73.829939
2   Bronx  Eastchester, Bronx  40.887556 -73.827806
3   Bronx    Fieldston, Bronx  40.895437 -73.905643
4   Bronx    Riverdale, Bronx  40.890834 -73.912585

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.

In [5]:
print('The New York dataframe has {} boroughs and {} neighborhoods.'.format(
        len(newyork_neighborhoods['Borough'].unique()),
        newyork_neighborhoods.shape[0]
    )
)

The New York dataframe has 5 boroughs and 306 neighborhoods.


#### Download the post codes and neighbor of Canada from Wiki page and scrape all the rows

In [6]:
source = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text
soup = BeautifulSoup(source, 'lxml')
table = soup.find('table', class_='wikitable')
table_rows = table.find_all('tr')

Define doesPostCodeExist function to check if the post code exist in current row

In [7]:
def doesPostalCodeExist(allRows, postCode, neighbourhood):
    for i, row in enumerate(allRows):
        if (row[0] == postCode):
            allRows[i][2] = allRows[i][2] + ', ' + neighbourhood
            return True
    return False

Build dataframe for all neighborhoods in Canada

In [8]:
allrows = []
for tr in table_rows:
    tds = tr.find_all('td')
    if (len(tds) == 3 and tds[1].text.strip() != 'Not assigned'): # check if the borough is Not Assigned
        if not doesPostalCodeExist(allrows, tds[0].text.strip(), tds[2].text.strip()):
            row = [tds[0].text.strip(), tds[1].text.strip(), tds[2].text.strip()]
            allrows.append(row)

headers = [header.text.strip() for header in table.find_all('th')]

headers = ['PostalCode','Borough','Neighborhood']

df = pd.DataFrame(allrows, columns=headers)
df['Neighborhood'] = np.where(df['Neighborhood'] == 'Not assigned', df['Borough'], df['Neighborhood']) # replace Neighbourhood if it is Not Assigned

Add latitude and longitude to dataframe from https://cocl.us/Geospatial_data

In [9]:
geocode = pd.read_csv("https://cocl.us/Geospatial_data")
geocode.rename(index=str, columns={"Postal Code": "PostalCode"}, inplace=True)
df = df.merge(geocode, left_on='PostalCode', right_on='PostalCode')

Get neighborhoods for boroughs contain word 'Toronto'

In [10]:
toronto_neighborhoods = df[df['Borough'].str.contains('Toronto')].reset_index(drop=True)
toronto_neighborhoods['Neighborhood'] = toronto_neighborhoods['Neighborhood'].astype(str) + '-Toronto'
toronto_neighborhoods.drop(columns=['PostalCode'], inplace =True)
toronto_neighborhoods.head()

Borough                       Neighborhood   Latitude  Longitude
0  Downtown Toronto  Harbourfront, Regent Park-Toronto  43.654260 -79.360636
1  Downtown Toronto   Ryerson, Garden District-Toronto  43.657162 -79.378937
2  Downtown Toronto             St. James Town-Toronto  43.651494 -79.375418
3      East Toronto                The Beaches-Toronto  43.676357 -79.293031
4  Downtown Toronto                Berczy Park-Toronto  43.644771 -79.373306

Check the number of boroughs and neighborhoods in Toronto

In [11]:
print('The Toronto dataframe has {} boroughs and {} neighborhoods.'.format(
        len(toronto_neighborhoods['Borough'].unique()),
        toronto_neighborhoods.shape[0]
    )
)

The Toronto dataframe has 4 boroughs and 38 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.

In [12]:
address = 'New York City, NY'

geolocator = Nominatim()
newyork_location = geolocator.geocode(address)
newyork_latitude = newyork_location.latitude
newyork_longitude = newyork_location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(newyork_latitude, newyork_longitude))

c:\users\tony\appdata\local\programs\python\python36\lib\site-packages\geopy\geocoders\osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of New York City are 40.7308619, -73.9871558.


#### Create a map of New York with neighborhoods superimposed on top.

In [13]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[newyork_latitude, newyork_longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(newyork_neighborhoods['Latitude'], newyork_neighborhoods['Longitude'], newyork_neighborhoods['Borough'], newyork_neighborhoods['Neighborhood']):
    label = neighborhood
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_newyork)  
        #parse_html=False).add_to(map_newyork)  
    
map_newyork

#### Use geopy library to get the latitude and longitude values of Toronto.

In [14]:
address = 'Toronto, Ontario'

geolocator = Nominatim()
toronto_location = geolocator.geocode(address)
toronto_latitude = toronto_location.latitude
toronto_longitude = toronto_location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(toronto_latitude, toronto_longitude))

c:\users\tony\appdata\local\programs\python\python36\lib\site-packages\geopy\geocoders\osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of Toronto are 43.653963, -79.387207.


#### Create a map of Toronto with neighborhoods superimposed on top.

In [15]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[toronto_latitude, toronto_longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_neighborhoods['Latitude'], toronto_neighborhoods['Longitude'], toronto_neighborhoods['Borough'], toronto_neighborhoods['Neighborhood']):
    label = neighborhood
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
        #parse_html=False).add_to(map_tornoto)  
    
map_toronto

#### Define Foursquare Credentials and Version

In [20]:
CLIENT_ID = 'XDWBCSTUFRBZZG2O0ZACKC3B0AHMX2HO51FM3RTV4VT0AXTV' # your Foursquare ID
CLIENT_SECRET = '5NDEV2LSSBCCRJY3L1R3XHTHDQTBQYCHJMZJMSYF2Z0TPYOJ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: XDWBCSTUFRBZZG2O0ZACKC3B0AHMX2HO51FM3RTV4VT0AXTV
CLIENT_SECRET:5NDEV2LSSBCCRJY3L1R3XHTHDQTBQYCHJMZJMSYF2Z0TPYOJ


#### Combine both cities' neighborhood.

In [21]:
neighborhoods = pd.concat([newyork_neighborhoods, toronto_neighborhoods])
neighborhoods_data = neighborhoods.reset_index(drop=True)
neighborhoods_data.shape

(344, 4)

<a id='item2'></a>

## 2. Explore Neighborhoods in Both Cities

#### Let's create a function to repeat the same process to all the neighborhoods in both cities

In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    LIMIT = 100 # limit of number of venues returned by Foursquare API

    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name, lat, lng)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *neighborhoods_venues*.

In [26]:
neighborhoods_venues = getNearbyVenues(names=neighborhoods_data['Neighborhood'],
                                   latitudes=neighborhoods_data['Latitude'],
                                   longitudes=neighborhoods_data['Longitude']
                                  )


Wakefield, Bronx 40.89470517661 -73.84720052054902
Co-op City, Bronx 40.87429419303012 -73.82993910812398
Eastchester, Bronx 40.887555677350775 -73.82780644716412
Fieldston, Bronx 40.89543742690383 -73.90564259591682
Riverdale, Bronx 40.890834493891305 -73.9125854610857
Kingsbridge, Bronx 40.88168737120521 -73.90281798724604
Marble Hill, Manhattan 40.87655077879964 -73.91065965862981
Woodlawn, Bronx 40.89827261213805 -73.86731496814176
Norwood, Bronx 40.87722415599446 -73.8793907395681
Williamsbridge, Bronx 40.88103887819211 -73.85744642974207
Baychester, Bronx 40.866858107252696 -73.83579759808117
Pelham Parkway, Bronx 40.85741349808865 -73.85475564017999
City Island, Bronx 40.84724670491813 -73.78648845267413
Bedford Park, Bronx 40.870185164975325 -73.8855121841913
University Heights, Bronx 40.85572707719664 -73.9104159619131
Morris Heights, Bronx 40.84789792606271 -73.91967159119565
Fordham, Bronx 40.86099679638654 -73.89642655981623
East Tremont, Bronx 40.84269615786053 -73.8873561

#### Let's check the size of the resulting dataframe

In [27]:
print(neighborhoods_venues.shape)
neighborhoods_venues.head()

(11724, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Wakefield, Bronx              40.894705              -73.847201   
1  Wakefield, Bronx              40.894705              -73.847201   
2  Wakefield, Bronx              40.894705              -73.847201   
3  Wakefield, Bronx              40.894705              -73.847201   
4  Wakefield, Bronx              40.894705              -73.847201   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato       40.894123       -73.845892   
1                                 Rite Aid       40.896521       -73.844680   
2  Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
3                         Carvel Ice Cream       40.890487       -73.848568   
4                            Dunkin Donuts       40.890631       -73.849027   

         Venue Category  
0          Dessert Shop  
1              Pharmacy  
2  Caribbean Restaurant  
3        Ice Cream Shop  
4            Donut Shop

Let's check how many venues were returned for each neighborhood

In [28]:
neighborhoods_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond-Toronto                                      100   
Allerton, Bronx                                                        27   
Annadale, Staten Island                                                12   
Arden Heights, Staten Island                                            5   
Arlington, Staten Island                                                6   
Arrochar, Staten Island                                                16   
Arverne, Queens                                                        15   
Astoria Heights, Queens                                                12   
Astoria, Queens                                                       100   
Auburndale, Queens                                                     19   
Bath Beach, Brooklyn                                                   50   
Battery Park City, Manhattan                                           97   
Bay Ridge, Brooklyn                                                    85   
Bay Terrace, Queens                                                    40   
Bay Terrace, Staten Island                                              9   
Baychester, Bronx                                                      21   
Bayside, Queens                                                        70   
Bayswater, Queens                                                       2   
Bedford Park, Bronx                                                    33   
Bedford Stuyvesant, Brooklyn                                           25   
Beechhurst, Queens                                                     10   
Bellaire, Queens                                                       12   
Belle Harbor, Queens                                                   15   
Bellerose, Queens                                                      19   
Belmont, Bronx                                                         93   
Bensonhurst, Brooklyn                                                  24   
Berczy Park-Toronto                                                    56   
Bergen Beach, Brooklyn                                                  6   
Blissville, Queens                                                     17   
Bloomfield, Staten Island                                               4   
Boerum Hill, Brooklyn                                                  84   
Borough Park, Brooklyn                                                 14   
Breezy Point, Queens                                                    6   
Briarwood, Queens                                                      12   
Brighton Beach, Brooklyn                                               44   
Broad Channel, Queens                                                   4   
Broadway Junction, Brooklyn                                            13   
Brockton, Exhibition Place, Parkdale Village-To...                     19   
Bronxdale, Bronx                                                       16   
Brooklyn Heights, Brooklyn                                            100   
Brookville, Queens                                                      2   
Brownsville, Brooklyn                                                  19   
Bulls Head, Staten Island                                              48   
Bushwick, Brooklyn                                                     72   
Business reply mail Processing Centre969 Easter...                     16   
Butler Manor, Staten Island                                             6   
CN Tower, Bathurst Quay, Island airport, Harbou...                     14   
Cabbagetown, St. James Town-Toronto                                    50   
Cambria Heights, Queens                                                13   
Canarsie, Brooklyn                                                      9   
Carnegie Hill, Manhattan                        

#### Let's find out how many unique categories can be curated from all the returned venues

In [29]:
print('There are {} uniques categories.'.format(len(neighborhoods_venues['Venue Category'].unique())))

There are 444 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [30]:
# one hot encoding
neighborhoods_onehot = pd.get_dummies(neighborhoods_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
neighborhoods_onehot['Neighborhood'] = neighborhoods_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [neighborhoods_onehot.columns[-1]] + list(neighborhoods_onehot.columns[:-1])
neighborhoods_onehot = neighborhoods_onehot[fixed_columns]

neighborhoods_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport  Airport Food Court  Airport Gate  \
0                   0        0                   0             0   
1                   0        0                   0             0   
2                   0        0                   0             0   
3                   0        0                   0             0   
4                   0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0         0       0                 0                       0   
1             0         0       0                 0                       0   
2             0         0       0                 0                       0   
3             0         0       0                 0                       0   
4             0         0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0                    0              0                0          0           0   
1                    0              0                0          0           0   
2                    0              0                0          0           0   
3                    0              0                0          0           0   
4                    0              0                0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Bath House  Beach  Beach Bar  \
0                 0                   0           0      0          0   
1                 0                   0           0      0          0   
2                 0                   0           0      0          0   
3                 0                   0           0      0          0   
4                 0                   0   

And let's examine the new dataframe size.

In [31]:
neighborhoods_onehot.shape

(11724, 444)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [32]:
neighborhoods_grouped = neighborhoods_onehot.groupby('Neighborhood').mean().reset_index()
neighborhoods_grouped

Neighborhood  Yoga Studio  \
0                     Adelaide, King, Richmond-Toronto     0.000000   
1                                      Allerton, Bronx     0.000000   
2                              Annadale, Staten Island     0.000000   
3                         Arden Heights, Staten Island     0.000000   
4                             Arlington, Staten Island     0.000000   
5                              Arrochar, Staten Island     0.000000   
6                                      Arverne, Queens     0.000000   
7                              Astoria Heights, Queens     0.000000   
8                                      Astoria, Queens     0.000000   
9                                   Auburndale, Queens     0.000000   
10                                Bath Beach, Brooklyn     0.000000   
11                        Battery Park City, Manhattan     0.000000   
12                                 Bay Ridge, Brooklyn     0.000000   
13                                 Bay Terrace, Queens     0.000000   
14                          Bay Terrace, Staten Island     0.000000   
15                                   Baychester, Bronx     0.000000   
16                                     Bayside, Queens     0.014286   
17                                   Bayswater, Queens     0.000000   
18                                 Bedford Park, Bronx     0.000000   
19                        Bedford Stuyvesant, Brooklyn     0.000000   
20                                  Beechhurst, Queens     0.100000   
21                                    Bellaire, Queens     0.000000   
22                                Belle Harbor, Queens     0.000000   
23                                   Bellerose, Queens     0.000000   
24                                      Belmont, Bronx     0.000000   
25                               Bensonhurst, Brooklyn     0.000000   
26                                 Berczy Park-Toronto     0.000000   
27                              Bergen Beach, Brooklyn     0.000000   
28                                  Blissville, Queens     0.000000   
29                           Bloomfield, Staten Island     0.000000   
30                               Boerum Hill, Brooklyn     0.023810   
31                              Borough Park, Brooklyn     0.000000   
32                                Breezy Point, Queens     0.000000   
33                                   Briarwood, Queens     0.000000   
34                            Brighton Beach, Brooklyn     0.000000   
35                               Broad Channel, Queens     0.000000   
36                         Broadway Junction, Brooklyn     0.000000   
37   Brockton, Exhibition Place, Parkdale Village-T...     0.000000   
38                                    Bronxdale, Bronx     0.000000   
39                          Brooklyn Heights, Brooklyn     0.050000   
40                                  Brookville, Queens     0.000000   
41                               Brownsville, Brooklyn     0.000000   
42                           Bulls Head, Staten Island     0.000000   
43                                  Bushwick, Brooklyn     0.000000   
44   Business reply mail Processing Centre969 Easte...     0.062500   
45                         Butler Manor, Staten Island     0.000000   
46   CN Tower, Bathurst Quay, Island airport, Harbo...     0.000000   
47                 Cabbagetown, St. James Town-Toronto     0.000000   
48                             Cambria Heights, Queens     0.000000   
49                                  Canarsie, Brooklyn     0.000000   
50                            Carnegie Hill, Manhattan     0.030612   
51                           Carroll Gardens, Brooklyn     0.010000   
52                                  Castle Hill, Bronx     0.000000   
53                    Castleton Corners, Staten Island     0.000000   
54                          Central Bay Street-Toronto     0.011628   
55                           Central Harlem, Manhattan     0.00000

#### Let's confirm the new size

In [35]:
neighborhoods_grouped.shape

(344, 444)

#### Let's print each neighborhood along with the top 5 most common venues

In [36]:
num_top_venues = 5

for hood in neighborhoods_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = neighborhoods_grouped[neighborhoods_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide, King, Richmond-Toronto----
             venue  freq
0      Coffee Shop  0.07
1             Café  0.05
2       Steakhouse  0.04
3  Thai Restaurant  0.04
4   Breakfast Spot  0.03


----Allerton, Bronx----
                venue  freq
0  Chinese Restaurant  0.11
1       Deli / Bodega  0.07
2         Pizza Place  0.07
3         Supermarket  0.07
4         Bus Station  0.07


----Annadale, Staten Island----
           venue  freq
0    Pizza Place  0.17
1   Dance Studio  0.08
2         Bakery  0.08
3  Deli / Bodega  0.08
4     Restaurant  0.08


----Arden Heights, Staten Island----
           venue  freq
0  Deli / Bodega   0.2
1    Pizza Place   0.2
2    Coffee Shop   0.2
3       Bus Stop   0.2
4       Pharmacy   0.2


----Arlington, Staten Island----
                 venue  freq
0        Boat or Ferry  0.17
1          Coffee Shop  0.17
2             Bus Stop  0.17
3  American Restaurant  0.17
4         Intersection  0.17


----Arrochar, Staten Island----
                      v

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [37]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [38]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = neighborhoods_grouped['Neighborhood']

for ind in np.arange(neighborhoods_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(neighborhoods_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood  \
0                     Adelaide, King, Richmond-Toronto   
1                                      Allerton, Bronx   
2                              Annadale, Staten Island   
3                         Arden Heights, Staten Island   
4                             Arlington, Staten Island   
5                              Arrochar, Staten Island   
6                                      Arverne, Queens   
7                              Astoria Heights, Queens   
8                                      Astoria, Queens   
9                                   Auburndale, Queens   
10                                Bath Beach, Brooklyn   
11                        Battery Park City, Manhattan   
12                                 Bay Ridge, Brooklyn   
13                                 Bay Terrace, Queens   
14                          Bay Terrace, Staten Island   
15                                   Baychester, Bronx   
16                                     Bayside, Queens   
17                                   Bayswater, Queens   
18                                 Bedford Park, Bronx   
19                        Bedford Stuyvesant, Brooklyn   
20                                  Beechhurst, Queens   
21                                    Bellaire, Queens   
22                                Belle Harbor, Queens   
23                                   Bellerose, Queens   
24                                      Belmont, Bronx   
25                               Bensonhurst, Brooklyn   
26                                 Berczy Park-Toronto   
27                              Bergen Beach, Brooklyn   
28                                  Blissville, Queens   
29                           Bloomfield, Staten Island   
30                               Boerum Hill, Brooklyn   
31                              Borough Park, Brooklyn   
32                                Breezy Point, Queens   
33                                   Briarwood, Queens   
34                            Brighton Beach, Brooklyn   
35                               Broad Channel, Queens   
36                         Broadway Junction, Brooklyn   
37   Brockton, Exhibition Place, Parkdale Village-T...   
38                                    Bronxdale, Bronx   
39                          Brooklyn Heights, Brooklyn   
40                                  Brookville, Queens   
41                               Brownsville, Brooklyn   
42                           Bulls Head, Staten Island   
43                                  Bushwick, Brooklyn   
44   Business reply mail Processing Centre969 Easte...   
45                         Butler Manor, Staten Island   
46   CN Tower, Bathurst Quay, Island airport, Harbo...   
47                 Cabbagetown, St. James Town-Toronto   
48                             Cambria Heights, Queens   
49                                  Canarsie, Brooklyn   
50                            Carnegie Hill, Manhattan   
51                           Carroll Gardens, Brooklyn   
52                                  Castle Hill, Bronx   
53                    Castleton Corners, Staten Island   
54                          Central Bay Street-Toronto   
55                           Central Harlem, Manhattan   
56                           Charleston, Staten Island   
57                                  Chelsea, Manhattan   
58                              Chelsea, Staten Island   
59   Chinatown, Grange Park, Kensington Market-Toronto   
60                                Chinatown, Manhattan   
61                                    Christie-Toronto   
62                        Church and Wellesley-Toronto   
63                                  City Island, Bronx   
64                                 City Line, Brooklyn   
65                             Civic Center, Manhattan   
66                            Claremont Village, Bronx   
67                                 Clason Point, Bronx   
68                              Clifton,

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [78]:
# set number of clusters
kclusters = 10

neighborhoods_grouped_clustering = neighborhoods_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(neighborhoods_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 6, 2, 5, 8, 5, 6, 6, 1, 1])

In [79]:
neighborhoods_merged = neighborhoods_data.sort_values('Neighborhood')

# add clustering labels
neighborhoods_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
neighborhoods_merged = neighborhoods_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

neighborhoods_merged.head() # check the last columns

Borough                      Neighborhood   Latitude  Longitude  \
313  Downtown Toronto  Adelaide, King, Richmond-Toronto  43.650571 -79.384568   
298             Bronx                   Allerton, Bronx  40.865788 -73.859319   
215     Staten Island           Annadale, Staten Island  40.538114 -74.178549   
241     Staten Island      Arden Heights, Staten Island  40.549286 -74.185887   
227     Staten Island          Arlington, Staten Island  40.635325 -74.165104   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
313               1           Coffee Shop                  Café   
298               6    Chinese Restaurant           Pizza Place   
215               2           Pizza Place            Restaurant   
241               5              Pharmacy         Deli / Bodega   
227               8           Coffee Shop          Intersection   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
313            Steakhouse       Thai Restaurant                   Bar   
298           Supermarket           Bus Station         Deli / Bodega   
215                Bakery                 Diner         Train Station   
241           Pizza Place           Coffee Shop              Bus Stop   
227              Bus Stop         Grocery Store   American Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
313        Breakfast Spot                   Gym                 Hotel   
298        Cosmetics Shop   Fried Chicken Joint    Spanish Restaurant   
215            Sports Bar          Dance Studio        Cosmetics Shop   
241         Women's Store                 Field  Ethiopian Restaurant   
227         Boat or Ferry         Women's Store                 Field   

    9th Most Common Venue 10th Most Common Venue  
313            Restaurant    American Restaurant  
298                   Spa   Fast Food Restaurant  
215                   Pub                   Park  
241           Event Space                Exhibit  
227  Fast Food Restaurant                   Farm

Finally, let's visualize the resulting clusters

In [80]:
# create map of New York
map_newyork_clusters = folium.Map(location=[newyork_latitude, newyork_longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

newyork_merged = neighborhoods_merged[neighborhoods_merged['Neighborhood'].str.endswith('-Toronto') == False]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'], newyork_merged['Neighborhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_newyork_clusters)
       
map_newyork_clusters

<a id='item5'></a>

In [81]:
# create map of Toronto
map_toronto_clusters = folium.Map(location=[toronto_latitude, toronto_longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

toronto_merged = neighborhoods_merged[neighborhoods_merged['Neighborhood'].str.endswith('-Toronto') == True]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_toronto_clusters)
       
map_toronto_clusters

## 5. Examine Clusters

#### Cluster 0

In [82]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 0,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
212     Oakwood, Staten Island                   Bar         Women's Store   
207  Port Ivory, Staten Island                   Bar         Women's Store   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
212  Fruit & Vegetable Store  Ethiopian Restaurant           Event Space   
207  Fruit & Vegetable Store  Ethiopian Restaurant           Event Space   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
212               Exhibit            Eye Doctor               Factory   
207               Exhibit            Eye Doctor               Factory   

    9th Most Common Venue 10th Most Common Venue  
212    Falafel Restaurant                   Farm  
207    Falafel Restaurant                   Farm

#### Cluster 1

In [83]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 1,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood  \
313                   Adelaide, King, Richmond-Toronto   
129                                    Astoria, Queens   
152                                 Auburndale, Queens   
127                       Battery Park City, Manhattan   
46                                 Bay Ridge, Brooklyn   
175                                Bay Terrace, Queens   
151                                    Bayside, Queens   
63                        Bedford Stuyvesant, Brooklyn   
34                                      Belmont, Bronx   
47                               Bensonhurst, Brooklyn   
310                                Berczy Park-Toronto   
87                               Boerum Hill, Brooklyn   
319  Brockton, Exhibition Place, Parkdale Village-T...   
64                          Brooklyn Heights, Brooklyn   
62                                  Bushwick, Brooklyn   
343  Business reply mail Processing Centre969 Easte...   
238                        Butler Manor, Staten Island   
337  CN Tower, Bathurst Quay, Island airport, Harbo...   
340                Cabbagetown, St. James Town-Toronto   
247                           Carnegie Hill, Manhattan   
66                           Carroll Gardens, Brooklyn   
311                         Central Bay Street-Toronto   
105                          Central Harlem, Manhattan   
239                          Charleston, Staten Island   
116                                 Chelsea, Manhattan   
244                             Chelsea, Staten Island   
335  Chinatown, Grange Park, Kensington Market-Toronto   
100                               Chinatown, Manhattan   
312                                   Christie-Toronto   
342                       Church and Wellesley-Toronto   
12                                  City Island, Bronx   
249                            Civic Center, Manhattan   
84                              Clinton Hill, Brooklyn   
113                                 Clinton, Manhattan   
65                               Cobble Hill, Brooklyn   
321             Commerce Court, Victoria Hotel-Toronto   
325                           Davisville North-Toronto   
331                                 Davisville-Toronto   
336  Deer Park, Forest Hill SE, Rathnelly, South Hi...   
318   Design Exchange, Toronto Dominion Centre-Toronto   
86                                  Downtown, Brooklyn   
283                                    Dumbo, Brooklyn   
81                             Dyker Heights, Brooklyn   
106                             East Harlem, Manhattan   
118                            East Village, Manhattan   
95                         East Williamsburg, Brooklyn   
39                               Edgewater Park, Bronx   
287                         Egbertville, Staten Island   
132                                   Elmhurst, Queens   
128                      Financial District, Manhattan   
341     First Canadian Place, Underground city-Toronto   
276                                Flatiron, Manhattan   
138                                   Flushing, Queens   
69                               Fort Greene, Brooklyn   
99                             Fort Hamilton, Brooklyn   
279                             Fulton Ferry, Brooklyn   
82                           Gerritsen Beach, Brooklyn   
68                                   Gowanus, Brooklyn   
126                                Gramercy, Manhattan   
229                            Grasmere, Staten Island   
49                                Greenpoint, Brooklyn   
117                       Greenwich Village, Manhattan   
103                        Hamilton Heights, Manhattan   
332             Harbord, University of Toronto-Toronto   
315  Harbourfront East, Toronto Islands, Union Stat...   
306                  Harbourfront, Regent Park-Toronto   
327              High Park, The Junction South-Toronto   
133                               Howard Beach, Queens   
301                            Hudson Ya

#### Cluster 2

In [84]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 2,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
215           Annadale, Staten Island                Pizza Place   
79               Bath Beach, Brooklyn                   Pharmacy   
10                  Baychester, Bronx                 Playground   
13                Bedford Park, Bronx                      Diner   
174                Beechhurst, Queens                Yoga Studio   
156                 Bellerose, Queens                Pizza Place   
80             Borough Park, Brooklyn                       Bank   
297                  Bronxdale, Bronx         Chinese Restaurant   
246         Bulls Head, Staten Island                   Bus Stop   
40                 Castle Hill, Bronx                Pizza Place   
208  Castleton Corners, Staten Island                Pizza Place   
90                City Line, Brooklyn                 Donut Shop   
253            Clifton, Staten Island              Train Station   
268          Concourse Village, Bronx       Fast Food Restaurant   
43                   Concourse, Bronx              Deli / Bodega   
134                    Corona, Queens         Mexican Restaurant   
55            Crown Heights, Brooklyn                Pizza Place   
71            Cypress Hills, Brooklyn        Fried Chicken Joint   
231       Dongan Hills, Staten Island                Pizza Place   
141             East Elmhurst, Queens                 Donut Shop   
17                East Tremont, Bronx                Pizza Place   
214        Eltingville, Staten Island                Pizza Place   
170              Far Rockaway, Queens                Pizza Place   
54                 Flatbush, Brooklyn              Deli / Bodega   
181               Floral Park, Queens         Chinese Restaurant   
16                     Fordham, Bronx                 Donut Shop   
135              Forest Hills, Queens                        Gym   
94               Georgetown, Brooklyn             Breakfast Spot   
155                 Glen Oaks, Queens                   Pharmacy   
233         Grant City, Staten Island                Pizza Place   
213        Great Kills, Staten Island                Pizza Place   
242         Greenridge, Staten Island             Scenic Lookout   
243  Heartland Village, Staten Island                 Restaurant   
19                High  Bridge, Bronx              Deli / Bodega   
289               Homecrest, Brooklyn              Grocery Store   
236           Huguenot, Staten Island         Italian Restaurant   
24                 Hunts Point, Bronx                  BBQ Joint   
160            Jamaica Center, Queens          Mobile Phone Shop   
57               Kensington, Brooklyn              Grocery Store   
157         Kew Gardens Hills, Queens                       Bank   
136               Kew Gardens, Queens         Chinese Restaurant   
299        Kingsbridge Heights, Bronx                Pizza Place   
5                  Kingsbridge, Bronx                Pizza Place   
187                Lindenwood, Queens                 Playground   
23                    Longwood, Bronx             Sandwich Place   
53        Manhattan Terrace, Brooklyn                Pizza Place   
6              Marble Hill, Manhattan             Sandwich Place   
83              Marine Park, Brooklyn                       Park   
142                   Maspeth, Queens                Pizza Place   
20                     Melrose, Bronx                Pizza Place   
290            Middle Village, Queens           Sushi Restaurant   
92                  Midwood, Brooklyn                Pizza Place   
262              Mill Basin, Brooklyn                Pizza Place   
15              Morris Heights, Bronx             Clothing Store   
33                 Morris Park, Bronx                Pizza Place   
25                  Morrisania, Bronx             Discount Store   
21                  Mott Haven, Bronx                 Donut Shop   
269                 Mount Eden, Bronx       Fast Food Restaurant   
270          

#### Cluster 3

In [85]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 3,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
303         Bayswater, Queens                  Park            Playground   
27        Clason Point, Bronx                  Park         Boat or Ferry   
4            Riverdale, Bronx                  Park            Food Truck   
338          Rosedale-Toronto                  Park                 Trail   
192        Somerville, Queens                  Park         Women's Store   
35      Spuyten Duyvil, Bronx                  Park                  Bank   
203  Todt Hill, Staten Island                  Park               Theater   

    3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  \
303         Women's Store          Electronics Store    English Restaurant   
27          Grocery Store  South American Restaurant                  Pool   
4                    Bank                        Gym                 Plaza   
338            Playground              Women's Store  Fast Food Restaurant   
192   Filipino Restaurant       Ethiopian Restaurant           Event Space   
35               Pharmacy            Thai Restaurant        Tennis Stadium   
203         Women's Store         Frozen Yogurt Shop  Ethiopian Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
303  Ethiopian Restaurant           Event Space               Exhibit   
27               Bus Stop        Scenic Lookout         Women's Store   
4           Women's Store  Fast Food Restaurant           Event Space   
338    English Restaurant  Ethiopian Restaurant           Event Space   
192               Exhibit            Eye Doctor               Factory   
35          Women's Store  Fast Food Restaurant           Event Space   
203           Event Space               Exhibit            Eye Doctor   

    9th Most Common Venue 10th Most Common Venue  
303            Eye Doctor                Factory  
27   Fast Food Restaurant            Event Space  
4                 Exhibit             Eye Doctor  
338               Exhibit             Eye Doctor  
192    Falafel Restaurant                   Farm  
35                Exhibit             Eye Doctor  
203               Factory     Falafel Restaurant

#### Cluster 4

In [86]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 4,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
179  Neponsit, Queens                 Beach        Scenic Lookout   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
179         Women's Store   Empanada Restaurant  Ethiopian Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
179           Event Space               Exhibit            Eye Doctor   

    9th Most Common Venue 10th Most Common Venue  
179               Factory     Falafel Restaurant

#### Cluster 5

In [87]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 5,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
241     Arden Heights, Staten Island              Pharmacy   
228          Arrochar, Staten Island         Deli / Bodega   
194                 Bellaire, Queens         Deli / Bodega   
190             Belle Harbor, Queens                   Spa   
159                Briarwood, Queens         Deli / Bodega   
171            Broad Channel, Queens              Dive Bar   
193               Brookville, Queens                Market   
254           Concord, Staten Island         Deli / Bodega   
154               Douglaston, Queens         Deli / Bodega   
258          Elm Park, Staten Island    Italian Restaurant   
144                 Glendale, Queens               Brewery   
284     Manor Heights, Staten Island         Deli / Bodega   
206  Mariner's Harbor, Staten Island    Italian Restaurant   
232     Midland Beach, Staten Island                 Beach   
234    New Dorp Beach, Staten Island    Italian Restaurant   
195             North Corona, Queens         Deli / Bodega   
89              Ocean Hill, Brooklyn         Deli / Bodega   
205     Port Richmond, Staten Island         Deli / Bodega   
288                  Roxbury, Queens                 Beach   
252       Shore Acres, Staten Island    Italian Restaurant   
204       South Beach, Staten Island         Deli / Bodega   
28                Throgs Neck, Bronx         Deli / Bodega   
217       Tottenville, Staten Island    Italian Restaurant   
264                   Utopia, Queens         Deli / Bodega   
32                   Van Nest, Bronx           Pizza Place   
285       Willowbrook, Staten Island         Deli / Bodega   
7                    Woodlawn, Bronx         Deli / Bodega   

    2nd Most Common Venue            3rd Most Common Venue  \
241         Deli / Bodega                      Pizza Place   
228    Italian Restaurant                         Bus Stop   
194           Supermarket               Chinese Restaurant   
190                 Beach                    Deli / Bodega   
159             Pet Store                      Bus Station   
171         Deli / Bodega                      Pizza Place   
193         Deli / Bodega                Fish & Chips Shop   
254    Chinese Restaurant                             Park   
154    Italian Restaurant               Chinese Restaurant   
258              Bus Stop                   Ice Cream Shop   
144         Deli / Bodega                Food & Drink Shop   
284      Sushi Restaurant                       Campground   
206         Deli / Bodega                         Bus Stop   
232              Bus Stop                       Restaurant   
234         Deli / Bodega                     Skating Rink   
195  Gym / Fitness Center                           Bakery   
89     Chinese Restaurant  Southern / Soul Food Restaurant   
205   Rental Car Location                       Food Truck   
288             Irish Pub                              Bar   
252              Bus Stop                     Intersection   
204                  Pier                            Beach   
28         Baseball Field               Italian Restaurant   
217         Deli / Bodega           Thrift / Vintage Store   
264    Chinese Restaurant                 Basketball Court   
32          Deli / Bodega                       Hookah Bar   
285    Chinese Restaurant                      Pizza Place   
7                     Pub                      Pizza Place   

    4th Most Common Venue      5th Most Common Venue  \
241           Coffee Shop                   Bus Stop   
228           Supermarket  Middle Eastern Restaurant   
194          Intersection         Italian Restaurant   
190    Italian Restaurant                 Donut Shop   
159    Mexican Restaurant                Coffee Shop   
171       Other Nightlife              Women's Store   
193  Ethiopian Restaurant                Event Space   
254  Gym / Fitness Center              Train Station   
154     Convenience Store                     

#### Cluster 6

In [88]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 6,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood       1st Most Common Venue  \
298                              Allerton, Bronx          Chinese Restaurant   
177                              Arverne, Queens                   Surf Spot   
266                      Astoria Heights, Queens                 Music Venue   
235                   Bay Terrace, Staten Island                 Supermarket   
91                        Bergen Beach, Brooklyn             Harbor / Marina   
278                           Blissville, Queens               Deli / Bodega   
172                         Breezy Point, Queens                       Beach   
51                      Brighton Beach, Brooklyn          Russian Restaurant   
282                  Broadway Junction, Brooklyn        Caribbean Restaurant   
60                         Brownsville, Brooklyn                        Park   
168                      Cambria Heights, Queens              Cosmetics Shop   
74                            Canarsie, Brooklyn                        Food   
267                     Claremont Village, Bronx                      Bakery   
1                              Co-op City, Bronx                 Bus Station   
149                        College Point, Queens               Deli / Bodega   
78                        Coney Island, Brooklyn        Caribbean Restaurant   
29                           Country Club, Bronx         Fried Chicken Joint   
221                        Ditmas Park, Brooklyn                    Pharmacy   
314         Dovercourt Village, Dufferin-Toronto                    Pharmacy   
56                       East Flatbush, Brooklyn          Chinese Restaurant   
72                       East New York, Brooklyn        Fast Food Restaurant   
2                             Eastchester, Bronx        Caribbean Restaurant   
45                               Edenwald, Bronx                 Fish Market   
176                             Edgemere, Queens               Metro Station   
255                  Emerson Hill, Staten Island  Construction & Landscaping   
300                            Erasmus, Brooklyn        Caribbean Restaurant   
3                               Fieldston, Bronx              Cosmetics Shop   
75                           Flatlands, Brooklyn        Fast Food Restaurant   
326  Forest Hill North, Forest Hill West-Toronto               Jewelry Store   
196                 Forest Hills Gardens, Queens                      Bakery   
158                        Fresh Meadows, Queens                 Bus Station   
226                  Graniteville, Staten Island                    Wine Bar   
50                           Gravesend, Brooklyn          Chinese Restaurant   
302                              Hammels, Queens                       Beach   
295                      Highland Park, Brooklyn                Liquor Store   
185                            Hillcrest, Queens          Italian Restaurant   
163                               Hollis, Queens               Shopping Mall   
182                           Holliswood, Queens           Mobile Phone Shop   
263                        Jamaica Hills, Queens                    Pharmacy   
188                            Laurelton, Queens        Caribbean Restaurant   
323                        Lawrence Park-Toronto                        Park   
189                          Lefrak City, Queens            Department Store   
77                     Manhattan Beach, Brooklyn              Sandwich Place   
76                         Mill Island, Brooklyn                        Food   
334          Moore Park, Summerhill East-Toronto                       Trail   
98                       Ocean Parkway, Brooklyn               Grocery Store   
41                              Olinville, Bronx                 Supermarket   
261                    Paerdegat Basin, Brooklyn            Asian Restaurant   
42                         Pelham Gardens, Bronx                  Donut Shop   
265                              Pom

#### Cluster 7

In [89]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 7,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
324  Roselawn-Toronto                Garden         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
324     Fish & Chips Shop  Ethiopian Restaurant           Event Space   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
324               Exhibit            Eye Doctor               Factory   

    9th Most Common Venue 10th Most Common Venue  
324    Falafel Restaurant                   Farm

#### Cluster 8

In [90]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 8,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
227      Arlington, Staten Island           Coffee Shop          Intersection   
245     Bloomfield, Staten Island     Recreation Center        Discount Store   
305      Fox Hills, Staten Island              Bus Stop        Sandwich Place   
202    Grymes Hill, Staten Island               Dog Run              Bus Stop   
198   New Brighton, Staten Island              Bus Stop         Deli / Bodega   
224      Park Hill, Staten Island              Bus Stop                 Hotel   
256  Randall Manor, Staten Island              Bus Stop                  Park   
286   Sandy Ground, Staten Island              Bus Stop                Market   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
227              Bus Stop         Grocery Store   American Restaurant   
245            Theme Park              Bus Stop  Ethiopian Restaurant   
305         Grocery Store         Women's Store  Ethiopian Restaurant   
202         Moving Target   American Restaurant           Fish Market   
198                  Park            Playground         Bowling Alley   
224    Athletics & Sports           Coffee Shop  Gym / Fitness Center   
256         Deli / Bodega           Pizza Place   Filipino Restaurant   
286          Liquor Store           Art Gallery                 Field   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
227         Boat or Ferry         Women's Store                 Field   
245           Event Space               Exhibit            Eye Doctor   
305           Event Space               Exhibit            Eye Doctor   
202               Exhibit            Eye Doctor               Factory   
198    Chinese Restaurant     Convenience Store        Discount Store   
224         Women's Store  Ethiopian Restaurant           Event Space   
256           Event Space               Exhibit            Eye Doctor   
286    English Restaurant  Ethiopian Restaurant           Event Space   

    9th Most Common Venue 10th Most Common Venue  
227  Fast Food Restaurant                   Farm  
245               Factory     Falafel Restaurant  
305               Factory     Falafel Restaurant  
202    Falafel Restaurant                   Farm  
198        Farmers Market                  Field  
224               Exhibit             Eye Doctor  
256               Factory     Falafel Restaurant  
286               Exhibit             Eye Doctor

#### Cluster 9

In [91]:
neighborhoods_merged.loc[neighborhoods_merged['Cluster Labels'] == 9,neighborhoods_merged.columns[[1] + list(range(5, neighborhoods_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
257  Howland Hook, Staten Island         Moving Target         Women's Store   
150           Whitestone, Queens                 Train       Bubble Tea Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
257     Fish & Chips Shop  Ethiopian Restaurant           Event Space   
150         Moving Target         Deli / Bodega         Women's Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
257               Exhibit            Eye Doctor               Factory   
150     Fish & Chips Shop           Event Space               Exhibit   

    9th Most Common Venue 10th Most Common Venue  
257    Falafel Restaurant                   Farm  
150            Eye Doctor                Factory